![](https://github.com/bigdata-icict/ETL-Dataiku-DSS/raw/master/tutoriais/pcdas_1.5.png)

# Notebook para criação de tabela de indicadores da PNS -  módulo R 2013 Saúde da Mulher - Parte 2

## Bibliotecas Utilizadas

In [ ]:
#Lendo pacotes necessários
library(survey)
library(ggplot2)
library(dplyr)
library(foreign)
library(forcats)
library(tidyverse)

## Carregando microdados da PNS

In [2]:
#Carregando banco de dados para R versão 3.5.0 ou superior
load("<coloque aqui o caminho para o arquivo dos microdados formato RDATA PNS 2013>")

#conferindo as dimensões (número de linhas e colunas)
dim("<Coloque aqui o nome do arquivo RDATA PNS 2013>")

[1] 222385   1000

## Definição do peso e filtragem de respondentes do questionário

In [3]:
#Selecionando registros válidos e calculando peso amostral - summary de verificação
pns2013.1<-pns2013 
pns2013.1<-pns2013 %>% filter(V0015==1)
pns2013.1<-pns2013.1 %>% mutate(peso_morador_selec=((V00291*(60202/145572211))))
pns2013.1<-pns2013.1 %>% filter(!is.na(peso_morador_selec))
summary(pns2013.1$peso_morador_selec)

     Min.   1st Qu.    Median      Mean   3rd Qu.      Max. 
 0.004156  0.243959  0.521557  1.000000  1.147413 31.179597 

## Criação de variáveis dos indicadores

In [4]:
#11. Proporção de mulheres de 18 a 49 anos de idade que tiveram relações sexuais nos últimos 12 meses, ainda menstruam e fazem uso de métodos para evitar a gravidez. - R011P
pns2013.1 <- pns2013.1 %>% mutate(R011P = ifelse(C006 == 2    &
                                                 (C008 >= 18  &
                                                  C008 <= 49) &
                                                 R026 == 1    &
                                                 R031 == 1    &
                                                 R034 == 1, 1, 2))
pns2013.1$R011P<-factor(pns2013.1$R011P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2013.1$R011P)

#12. Proporção (%) de mulheres de 18 a 49 anos de idade que já ficaram grávidas - R012P     
pns2013.1 <- pns2013.1 %>% mutate(R012P = ifelse(C006 == 2 & 
                                                 (C008 >= 18 &
                                                  C008 <= 49) &
                                                 R039 == 1, 1, 2))

pns2013.1$R012P<-factor(pns2013.1$R012P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2013.1$R012P)

#13. Proporção de mulheres de 18 a 49 anos de idade que fazem algum tratamento para engravidar. - R013P
pns2013.1 <- pns2013.1 %>% mutate(R013P = if_else(C006 == 2 & 
                                                 (C008 >= 18 &
                                                  C008 <= 49) &
                                                 (R037 == 1 | 
                                                  R037 == 2), 1, 2, 
                                                     missing=2))
pns2013.1$R013P<-factor(pns2013.1$R013P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2013.1$R013P)

Sim   Não  NA's 
10544 48999   659

Sim   Não 
16811 43391

Sim   Não 
  550 59652

## Definições de abrangências

### Situação urbana ou rural

In [5]:
#Situação Urbano ou Rural
pns2013.1 <- pns2013.1 %>% rename(Sit_Urbano_Rural=V0026)
pns2013.1$Sit_Urbano_Rural<-factor(pns2013.1$Sit_Urbano_Rural, levels=c(1,2), labels=c("Urbano", "Rural"))
summary(pns2013.1$Sit_Urbano_Rural)

Urbano  Rural 
 49245  10957

### UF

In [6]:
#Estados - UFs
pns2013.1 <- pns2013.1 %>% rename(Unidades_da_Federacao=V0001)
pns2013.1$Unidades_da_Federacao<-factor(pns2013.1$Unidades_da_Federacao, levels=c(11,12,13,14,15,16,17,21,22,23,24,25,26,27,28,29,31,32,33,35,41,42,43,50,51,52,53),
                                       label=c("Rondônia","Acre","Amazonas","Roraima","Pará","Amapá","Tocantins","Maranhão","Piauí","Ceará",
                                        "Rio Grande do Norte","Paraíba","Pernambuco","Alagoas","Sergipe","Bahia",
                                        "Minas Gerais","Espírito Santo","Rio de Janeiro","São Paulo",
                                        "Paraná","Santa Catarina","Rio Grande do Sul", 
                                        "Mato Grosso do Sul","Mato Grosso","Goiás","Distrito Federal"))
summary(pns2013.1$Unidades_da_Federacao)

Rondônia                Acre            Amazonas             Roraima 
               1694                1814                2586                1591 
               Pará               Amapá           Tocantins            Maranhão 
               2004                1332                1515                1774 
              Piauí               Ceará Rio Grande do Norte             Paraíba 
               1804                2560                1691                1943 
         Pernambuco             Alagoas             Sergipe               Bahia 
               2591                1748                1553                2641 
       Minas Gerais      Espírito Santo      Rio de Janeiro           São Paulo 
               3779                1724                3486                5305 
             Paraná      Santa Catarina   Rio Grande do Sul  Mato Grosso do Sul 
               3012                1623                2913                1809 
        Mato Grosso               Goiás    Distrito Federal 
               1476                2423                1811

### Grandes Regiões

In [7]:
#Grandes Regiões
pns2013.1 <- pns2013.1 %>% 
  mutate(GrandesRegioes = fct_collapse(Unidades_da_Federacao, 
                                          `Norte` = c("Rondônia","Acre","Amazonas","Roraima","Pará", "Amapá","Tocantins"),
                                          `Nordeste` = c("Maranhão", "Piauí", "Ceará", "Rio Grande do Norte", "Paraíba","Pernambuco", "Alagoas","Sergipe","Bahia"),
                                          `Sudeste` = c("Minas Gerais", "Espírito Santo","Rio de Janeiro", "São Paulo"), 
                                          `Sul` = c("Paraná", "Santa Catarina", "Rio Grande do Sul"),
                                          `Centro-Oeste`= c("Mato Grosso do Sul","Mato Grosso", "Goiás", "Distrito Federal")))
summary(pns2013.1$GrandesRegioes)

Norte     Nordeste      Sudeste          Sul Centro-Oeste 
       12536        18305        14294         7548         7519

### Capital

In [8]:
#Capital
pns2013.1<- pns2013.1 %>% mutate(Capital= fct_collapse(Unidades_da_Federacao,
                                        `Porto Velho`= "Rondônia", 
                                        `Boa Vista`= "Roraima",              
                                        `Rio Branco`= "Acre", 
                                        `Manaus` = "Amazonas",
                                        `Belém` = "Pará" ,
                                        `Macapá`= "Amapá",
                                        `Palmas` = "Tocantins",
                                        `São Luís` = "Maranhão",
                                        `Teresina`= "Piauí" ,
                                        `Fortaleza`= "Ceará",
                                        `Natal`= "Rio Grande do Norte",
                                        `João Pessoa`= "Paraíba",
                                        `Recife`= "Pernambuco",
                                        `Maceió`= "Alagoas",
                                        `Aracaju`= "Sergipe",
                                        `Salvador`= "Bahia",
                                        `Belo Horizonte`= "Minas Gerais",
                                        `Vitória`= "Espírito Santo",
                                        `Rio de Janeiro`= "Rio de Janeiro",
                                        `São Paulo`= "São Paulo",
                                        `Curitiba`= "Paraná",
                                        `Florianópolis`= "Santa Catarina",
                                        `Porto Alegre`= "Rio Grande do Sul",
                                        `Campo Grande`=  "Mato Grosso do Sul",
                                        `Cuiabá`= "Mato Grosso",
                                        `Goiânia` = "Goiás",
                                        `Brasília`= "Distrito Federal")
        )
summary(pns2013.1$Capital)

Porto Velho     Rio Branco         Manaus      Boa Vista          Belém 
          1694           1814           2586           1591           2004 
        Macapá         Palmas       São Luís       Teresina      Fortaleza 
          1332           1515           1774           1804           2560 
         Natal    João Pessoa         Recife         Maceió        Aracaju 
          1691           1943           2591           1748           1553 
      Salvador Belo Horizonte        Vitória Rio de Janeiro      São Paulo 
          2641           3779           1724           3486           5305 
      Curitiba  Florianópolis   Porto Alegre   Campo Grande         Cuiabá 
          3012           1623           2913           1809           1476 
       Goiânia       Brasília 
          2423           1811

### Faixa Etária

In [9]:
#Faixas Etárias
pns2013.1 <-  pns2013.1 %>% mutate(faixa_idade=cut(C008,
  breaks = c(17.99, 29.99, 44.99, 59.99),
  labels = c("18 a 29 anos",
             "30 a 44 anos",
             "45 a 59 anos"), 
  ordered_result = TRUE, right = TRUE))
summary(pns2013.1$faixa_idade)

18 a 29 anos 30 a 44 anos 45 a 59 anos         NA's 
       14321        20242        14462        11177

### Raça

In [10]:
#Raça
pns2013.1 <- pns2013.1 %>% 
                mutate(Raca= ifelse(C009==1, 1, 
                             ifelse(C009==2, 2, 
                             ifelse(C009==4, 3, 9))))

pns2013.1$Raca<-factor(pns2013.1$Raca,
                       levels=c(1,2,3),
                       labels=c("Branca", "Preta", "Parda"))
summary(pns2013.1$Raca)

Branca  Preta  Parda   NA's 
 24106   5631  29512    953

### Renda per capta

In [11]:
# Rendimento domiciliar per capita
pns2013.1 <-  pns2013.1 %>% mutate(rend_per_capita=cut(VDF003,
  breaks = c(-Inf, 339, 678, 1356, 2034, Inf),
  labels=c("Até 1/2 SM",
           "1/2 até 1 SM",
           "1 até 2 SM",
           "2 até 3 SM",
           "Mais de 3 SM"), 
  ordered_result = TRUE, right = TRUE, na.exclude= TRUE))
summary(pns2013.1$rend_per_capita)

Até 1/2 SM 1/2 até 1 SM   1 até 2 SM   2 até 3 SM Mais de 3 SM         NA's 
       14256        17504        15493         5335         7603           11

### Escolaridade

In [12]:
# Escolaridade
pns2013.1 <- pns2013.1 %>% mutate(gescol = ifelse(VDD004A %in% 1:2, 1, 
                        ifelse(VDD004A%in% 3:4, 2, 
                        ifelse(VDD004A%in% 5:6, 3,
                        ifelse(is.na(VDD004A)==TRUE, NA_real_, 4)))))

pns2013.1$gescol<-factor(pns2013.1$gescol, levels=c(1,2,3,4), 
                                  labels=c("Fundamental incompleto ou equivalente",
                                           "Médio incompleto ou equivalente",
                                           "Superior incompleto ou equivalente",
                                           "Superior completo"))
summary(pns2013.1$gescol)

Fundamental incompleto ou equivalente       Médio incompleto ou equivalente 
                                24083                                  9215 
   Superior incompleto ou equivalente                     Superior completo 
                                19149                                  7755

## Criando indicadores

### Filtrando base de indicadores

In [13]:
#Selecionando variáveis para cálculo de indicadores no survey_R
pns2013Rsurvey <- pns2013.1 %>% select("V0024","UPA_PNS","peso_morador_selec", "C006", "R011P",
                                       "R012P","R013P","C008","V0031","R026","R031","Sit_Urbano_Rural",
                                       "Unidades_da_Federacao","GrandesRegioes","Capital","faixa_idade",
                                       "Raca","rend_per_capita","gescol")
# summary(pns2013Rsurvey)

### Exporta tabela filtrada com os dados específicos - Módulo R 2013

In [14]:
#Salvando csv para cálculo de indicadores no survey
diretorio_saida <- "<coloque aqui o diretório>"
write.csv(pns2019Rsurvey, file.path(diretorio_saida, "pns2013R2survey.csv"))

### Cria plano amostral complexo

In [15]:
desPNSR=svydesign(id=~UPA_PNS,
                  strat=~V0024,
                  weight=~peso_morador_selec,
                  nest=TRUE,
                  data=pns2013Rsurvey)
desPNSR0__P=subset(desPNSR, (C008>=18 & C008<=49) & C006==2)

In [19]:
#survey design R011P
desPNSR011P=subset(desPNSR0__P, !is.na(R011P) & R026 == 1  &  R031 == 1)
desPNSR011P_C=subset(desPNSR011P,  V0031==1)
desPNSR011P_R=subset(desPNSR011P,  !is.na(Raca))
desPNSR011P_FX=subset(desPNSR011P, !is.na(faixa_idade))
desPNSR011P_RE=subset(desPNSR011P, !is.na(rend_per_capita))

In [20]:
#survey design R012P
desPNSR012P=subset(desPNSR0__P, !is.na(R012P))
desPNSR012P_C=subset(desPNSR012P, V0031==1)
desPNSR012P_R=subset(desPNSR012P, !is.na(Raca))
desPNSR012P_FX=subset(desPNSR012P, !is.na(faixa_idade))
desPNSR012P_RE=subset(desPNSR012P, !is.na(rend_per_capita))

In [21]:
#survey design R013P
desPNSR013P=subset(desPNSR0__P, !is.na(R013P))
desPNSR013P_C=subset(desPNSR013P, V0031==1)
desPNSR013P_R=subset(desPNSR013P, !is.na(Raca))
desPNSR013P_FX=subset(desPNSR013P, !is.na(faixa_idade))
desPNSR013P_RE=subset(desPNSR013P, !is.na(rend_per_capita))

### Criação da tabela de indicadores

In [22]:
matrizIndicadores = data.frame()

#### Definição de variáveis para iteração dos indicadores

In [23]:
ListaIndicadores = c(~R011P,~R012P,~R013P)
ListaIndicadoresTexto = c("R011P","R012P","R013P")
ListaTotais = c('Brasil','Capital')
Ano <- "2013"

In [24]:
ListaDominios = c(~Raca,~rend_per_capita,~faixa_idade,~Sit_Urbano_Rural,
                   ~Unidades_da_Federacao,~GrandesRegioes,~Capital,~gescol)
ListaDominiosTexto = c("raça","rend_per_capita","faixa_idade","urb_rur",
                        "uf","região","capital","gescol")

#### Preenchendo a tabela de indicadores
Essas iterações rodam por indicador, abrangência e por design

In [25]:
#Cálculo dos indicadores usando o pacote survey 
i <- 0
matrizIndicadores = data.frame()
#Para cada indicador
for(indicador in ListaIndicadores){
    i <- i + 1
    j <- 1
    print(indicador)
    #Para cada dominio
    for (dominio in ListaDominios){
               #design especifico para capital que é subconjunto do dataframe total
               if (ListaDominiosTexto[j]=="capital"){
                   #designs especificos por variavel que são subconjuntos do dataset total
                   if(ListaIndicadoresTexto[i] == "R011P"){
                     dataframe_indicador<-svyby(indicador, dominio, desPNSR011P_C, svymean,vartype= c("ci", "cv"))
                   }
                   else if(ListaIndicadoresTexto[i] == "R012P"){
                     dataframe_indicador<-svyby(indicador, dominio, desPNSR012P_C, svymean,vartype= c("ci", "cv"))
                   }
                   else {
                     dataframe_indicador<-svyby(indicador, dominio, desPNSR013P_C, svymean,vartype= c("ci", "cv"))
                   }
               #Uso design do subconjunto para raça/cor que inclui preta,branca e parda as outras 
               # conjunto com nulos
               } else if (ListaDominiosTexto[j]=="raça"){
                   if(ListaIndicadoresTexto[i] == "R011P"){
                     dataframe_indicador<-svyby(indicador, dominio, desPNSR011P_R, svymean,vartype= c("ci", "cv"))
                   }
                   else if(ListaIndicadoresTexto[i] == "R012P"){
                     dataframe_indicador<-svyby(indicador, dominio, desPNSR012P_R, svymean,vartype= c("ci", "cv"))
                   }
                   else {
                     dataframe_indicador<-svyby(indicador, dominio, desPNSR013P_R, svymean,vartype= c("ci", "cv"))
                   }

               } else if (ListaDominiosTexto[j]=="rend_per_capita"){
               #design geral para o subconjunto de renda
               # conjunto com nulos
                   if(ListaIndicadoresTexto[i] == "R011P"){
                     dataframe_indicador<-svyby(indicador, dominio, desPNSR011P_RE, svymean,vartype= c("ci", "cv"))
                   }
                   else if(ListaIndicadoresTexto[i] == "R012P"){
                     dataframe_indicador<-svyby(indicador, dominio, desPNSR012P_RE, svymean,vartype= c("ci", "cv"))
                   }
                   else {
                     dataframe_indicador<-svyby(indicador, dominio, desPNSR013P_RE, svymean,vartype= c("ci", "cv"))
                   }
               #design geral para o subconjunto de escolaridade
               # conjunto com nulos
               } else if (ListaDominiosTexto[j]=="faixa_idade"){
                   if(ListaIndicadoresTexto[i] == "R011P"){
                     dataframe_indicador<-svyby(indicador, dominio, desPNSR011P, svymean,vartype= c("ci", "cv"))
                   }
                   else if(ListaIndicadoresTexto[i] == "R012P"){
                     dataframe_indicador<-svyby(indicador, dominio, desPNSR012P, svymean,vartype= c("ci", "cv"))
                   }
                   else {
                     dataframe_indicador<-svyby(indicador, dominio, desPNSR013P_FX, svymean,vartype= c("ci", "cv"))
                   }
               } else if(ListaIndicadoresTexto[i] == "R011P"){
                     dataframe_indicador<-svyby(indicador, dominio, desPNSR011P, svymean,vartype= c("ci", "cv"))
                   } else if(ListaIndicadoresTexto[i] == "R012P"){
                     dataframe_indicador<-svyby(indicador, dominio, desPNSR012P, svymean,vartype= c("ci", "cv"))
                   }
                   else {
                     print(indicador)
                     print(dominio)
                     dataframe_indicador<-svyby(indicador, dominio, desPNSR013P, svymean,vartype= c("ci", "cv"))
                   }
               #União do dataframe de indicadores no formato do painel disponibilizado para PNS
               
               dataframe_indicador<-data.frame(dataframe_indicador)
               
               colnames(dataframe_indicador) <- c("abr_nome","Sim","Nao","LowerS","LowerN","UpperS","UpperN","cvS","cvN")
               dataframe_indicador$Indicador <- ListaIndicadoresTexto[i]
               dataframe_indicador$abr_tipo <- ListaDominiosTexto[j]
               dataframe_indicador$Ano <- Ano
               dataframe_indicador <- dataframe_indicador %>% select("abr_tipo","abr_nome","Ano","Indicador","Sim","LowerS","UpperS","cvS")
               matrizIndicadores <-rbind(matrizIndicadores,dataframe_indicador)
               j <- j + 1
    }
}

~R011P
~R012P
~R013P
~R013P
~Sit_Urbano_Rural
~R013P
~Unidades_da_Federacao
~R013P
~GrandesRegioes
~R013P
~gescol


#### Criando a tabela pela abrangência total

In [26]:
matriz_totais <- data.frame()

#### Preenchendo a tabela com as abrangencia Brasil e total das capitais

In [27]:
i=0
matriz_totais <- data.frame()
#para cada indicador
for(indicador in ListaIndicadores){
    i <- i+1
    #para os totais Brasil e total das capitais
    for(total in ListaTotais){
        dataframe_indicador <- data.frame()
        #Uso do design que é subconjunto do dataset para cada Capital
        if (total == "Capital"){
                   #Indicadores que são subconjunto do dataset tot
                   if(ListaIndicadoresTexto[i] == "R011P"){
                           dataframe_indicador <- svymean(indicador, desPNSR011P_C)
                   }
                   else if(ListaIndicadoresTexto[i] == "R012P"){
                       dataframe_indicador <- svymean(indicador, desPNSR012P_C)
                   }
                   else {
                       dataframe_indicador <- svymean(indicador, desPNSR013P_C)
                   }
        } else {
                   if(ListaIndicadoresTexto[i] == "R011P"){
                           dataframe_indicador <- svymean(indicador, desPNSR011P)
                   }
                   else if(ListaIndicadoresTexto[i] == "R012P"){
                       dataframe_indicador <- svymean(indicador, desPNSR012P)
                   }
                   else {
                       dataframe_indicador <- svymean(indicador, desPNSR013P)
                   }
        }

       intervalo_confianca <- confint(dataframe_indicador)
       coeficiente_variacao <- cv(dataframe_indicador)
       dataframe_indicador <- cbind(data.frame(dataframe_indicador),data.frame(intervalo_confianca))
       dataframe_indicador <- cbind(data.frame(dataframe_indicador),data.frame(coeficiente_variacao))

       dataframe_indicador <- dataframe_indicador %>% 
                               select('mean','X2.5..','X97.5..',coeficiente_variacao) 
        
       dataframe_indicador <- dataframe_indicador %>% 
                                 slice(1)
       colnames(dataframe_indicador) <- c('Sim','LowerS','UpperS','cvS')
       dataframe_indicador <- dataframe_indicador %>% 
                               select('Sim','LowerS','UpperS','cvS')
       dataframe_indicador$Indicador <- ListaIndicadoresTexto[i]
       dataframe_indicador$abr_tipo <- "total"
       dataframe_indicador$abr_nome <- total
       dataframe_indicador$Ano <- Ano 
       dataframe_indicador <- dataframe_indicador %>% 
                            select("abr_tipo","abr_nome","Ano","Indicador",'Sim','LowerS','UpperS','cvS')
       
       matriz_totais <-rbind(matriz_totais,dataframe_indicador)
    }
}

In [28]:
matriz_totais

abr_tipo abr_nome Ano  Indicador Sim        LowerS     UpperS    
R011PSim  total    Brasil   2013 R011P     0.61113107 0.59805269 0.62420945
R011PSim1 total    Capital  2013 R011P     0.63545398 0.61953582 0.65137215
R012PSim  total    Brasil   2013 R012P     0.69183920 0.68022450 0.70345391
R012PSim1 total    Capital  2013 R012P     0.65518756 0.64054336 0.66983176
R013PSim  total    Brasil   2013 R013P     0.02616984 0.02243197 0.02990772
R013PSim1 total    Capital  2013 R013P     0.02303964 0.01899242 0.02708686
          cvS        
R011PSim  0.010918713
R011PSim1 0.012780883
R012PSim  0.008565543
R012PSim1 0.011403861
R013PSim  0.072874575
R013PSim1 0.089625758

#### Unindo tabela de indicadores e de totais

In [29]:
matrizIndicadores<-rbind(matrizIndicadores,matriz_totais)

In [30]:
unique(matrizIndicadores$abr_tipo)

[1] "raça"            "rend_per_capita" "faixa_idade"     "urb_rur"        
[5] "uf"              "região"          "capital"         "gescol"         
[9] "total"

In [42]:
matrizIndicadores[matrizIndicadores$abr_tipo=='urb_rur' & 
                  matrizIndicadores$Indicador=='R013P', ]

abr_tipo abr_nome Ano  Indicador Sim        LowerS     UpperS    
Urbano2 urb_rur  Urbano   2013 R013P     0.02585151 0.02179281 0.02991021
Rural2  urb_rur  Rural    2013 R013P     0.02831154 0.01889467 0.03772840
        cvS       
Urbano2 0.08010382
Rural2  0.16970504

#### Visualizando tabela de indicadores

#### Exportando tabela de indicadores calculados - Módulo R 2013

In [50]:
diretorio_saida <- "<coloque aqui o diretório>"
write.table(matrizIndicadores,file=paste0(diretorio_saida,"Indicadores_2013R2_R.csv"),sep = ";",dec = ",",row.names = FALSE)